# **This is the implementation code of preparing dataset and training process for Defect Detection**

In [5]:
%%shell
git config --global user.email "ahmet.nasri@daimia.com"
git config --global user.name "Ahmet Nasri"
cd "/content/drive/My Drive/Colab Notebooks/faultdet"
git pull
git add -A
git commit -m "user friend code"
git push

Already up to date.
[master 8c4d7d2] user friend code
 1 file changed, 1 insertion(+), 1 deletion(-)
Counting objects: 3, done.
Delta compression using up to 2 threads.
Compressing objects: 100% (3/3), done.
Writing objects: 100% (3/3), 629 bytes | 629.00 KiB/s, done.
Total 3 (delta 2), reused 0 (delta 0)
remote: Resolving deltas: 100% (2/2), completed with 2 local objects.
To https://github.com/daimia-ai/faultdet
   6a2944b..8c4d7d2  master -> master


In [ ]:
#import your drive
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
#uncompress your dataset, if it is a rar file
!unrar x "/content/drive/My Drive/DAIMIA/syntetic data.rar" "/content"
#!unzip "/content/drive/My Drive/DAIMIA/syntetic data.zip" -d "/dat"

In [ ]:
#downlaod the repository of Tensorflow model project which contains a collection of research model implementations in TensorFlow 1 or 2 by researchers
!git clone https://github.com/ansarisam/models.git

In [ ]:
#Install Google protobuf compiler and otherdependencies

!sudo apt-get install protobuf-compiler python-pil python-lxml python-tk

In [ ]:
#Install dependencies
%%shell
 cd models/research
 pwd
 protoc object_detection/protos/*.proto --python_out=.
 pip install --user Cython
 pip install --user contextlib2
 pip install --user pillow
 pip install --user lxml
 pip install --user jupyter
 pip install --user matplotlib

In [ ]:
#Build models project
%%shell
 export PYTHONPATH=$PYTHONPATH:/content/models/research:/content/models/research/slim
 cd /content/models/research
 python setup.py build
 python setup.py install


In [ ]:
#since the model is bases on tensorflow 1.x version, we have to install tensorflow 1.15
!pip install tensorflow==1.15

In [ ]:
#%tensorflow_version 1.x
import tensorflow as tf


In [ ]:
tf.test.gpu_device_name()

'/device:GPU:0'

In [ ]:
print(tf.__version__)

1.15.0


In [ ]:
#converting the dataset from PNG to JPG
from pathlib import Path
from PIL import Image

inputPath = Path("/content/data/IMAGES")
inputFiles = inputPath.glob("*.png")
outputPath = Path("/content/data/1")
for f in inputFiles:
    outputFile = outputPath / Path(f.stem + ".jpg")
    im = Image.open(f)
    im.save(outputFile)

In [ ]:
"""Convert XML derived dict to tf.Example proto.
Notice that this function normalizes the bounding box coordinates
provided by the raw data.

 Args:
 data: dict holding PASCAL XML fields for a single image
 dataset_directory: Path to root directory holding PASCAL dataset
 label_map_dict: A map from string label names to integers ids.
 ignore_difficult_instances: Whether to skip difficult instances in the
 dataset (default: False).
 image_subdirectory: String specifying subdirectory within the dataset directory holding the actual image data.

Returns:
example: The converted tf.Example.
Raises: ValueError: if the image pointed to by data[filename] is not avalid JPEG """

In [ ]:
# at this block, we will perform the process of converting the data to TFRecord, as it is required to feed the model
# notice that the defining of flags must be performed just one time, that means if you run the code for the second time 
# it will show an error, to solve this, take the lines where the flags are defined as comment as you run the code for the second time.
# As a result of this block you will have your data as a TFRecords files in the directory you specified.


# We need a mapping file that maps the class index with the class name. This file
# contains JSON content and typically has the extension .pbtxt. 
# you can download the class map from this link https://drive.google.com/file/d/1Q3xc7eR9BFCv-DuX_lk2FM5IRitgnASk/view?usp=sharing
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import hashlib
import io
import logging
import os

from lxml import etree
import PIL.Image

import tensorflow as tf
%cd /content/models/research
from object_detection.utils import dataset_util
from object_detection.utils import label_map_util
import random
#flags =tf.compat.v1.flags
flags = tf.app.flags

#FLAGS = flags.FLAGS
flags.DEFINE_string('data_dir', '/content/data', 'Root directory to raw PASCAL VOC dataset.')

flags.DEFINE_string('annotations_dir', 'ANNOTATIONS','(Relative) path to annotations directory.')
flags.DEFINE_string('image_dir', '1','(Relative) path to images directory.')

flags.DEFINE_string('output_path', '/content/drive/My Drive/DAIMIA/Synthetic Date/TFRecord', 'Path to output TFRecord')
flags.DEFINE_string('label_map_path', '/content/defect_label_map.pbtxt','Path to label map proto')

flags.DEFINE_boolean('ignore_difficult_instances', False, 'Whether toignore difficult instances')
FLAGS = flags.FLAGS
 
# This function generates a list of images for training andvalidation.
def create_trainval_list(data_dir):
  trainval_filename = os.path.abspath(os.path.join(data_dir,"trainval.txt"))
  trainval = open(os.path.abspath(trainval_filename), "w")
  files = os.listdir(os.path.join(data_dir, FLAGS.image_dir))
  for d in files:
    absfile =os.path.abspath(os.path.join(data_dir, FLAGS.image_dir, d))
    trainval.write(absfile+"\n")
    print(absfile)
  trainval.close()
 

def dict_to_tf_example(data,
 dataset_directory,
 label_map_dict,
 ignore_difficult_instances=False,image_subdirectory= '1',):
# image_subdirectory=FLAGS.image_dir):






  data['filename'] = data['filename'].replace('C:/Users/teozk/DaimiaSimulation/Assets/StreamingAssets/SyntheticData/Dataset_2020-08-14_02-43-59/', '')
  filename = data['filename'].replace('.png', '')
  #print('filename',type(data['filename']))
  #print(type(filename))

  if filename.find(".jpg") < 0:
    filename = filename+".jpg"
  img_path = os.path.join("",image_subdirectory, filename)
  full_path = os.path.join(dataset_directory, img_path)

  with tf.gfile.GFile(full_path, 'rb') as fid:
    encoded_jpg = fid.read()
  encoded_jpg_io = io.BytesIO(encoded_jpg)
  image = PIL.Image.open(encoded_jpg_io)
  if image.format != 'JPEG':
    raise ValueError('Image format not JPEG')
  key = hashlib.sha256(encoded_jpg).hexdigest()

  width = int(data['source']['width'])
  height = int(data['source']['height'])

  xmin = []
  ymin = []
  xmax = []
  ymax = []
  classes = []
  classes_text = []
  truncated = []
  poses = []
  difficult_obj = []
  if 'object' in data:
    for obj in data['object']:
      difficult = bool(int(obj['difficult']))
      if ignore_difficult_instances and difficult:
        continue
      difficult_obj.append(int(difficult))
      xmin.append(float(obj['bndbox']['xmin']) / width)
      if float(obj['bndbox']['xmin']) >= 300:
        print('xmin',float(obj['bndbox']['xmin']))
        print(data['filename'])
      ymin.append(float(obj['bndbox']['ymin']) / height)
      if float(obj['bndbox']['ymin']) >= 300:
        print('ymin',float(obj['bndbox']['ymin']))
        print(data['filename'])                   
      #print('ymin',"{:.4f}".format(1080-float(obj['bndbox']['ymin'])))
      #print('ymin',type(obj['bndbox']['ymin']))
      xmax.append(float(obj['bndbox']['xmax']) / width)
      if float(obj['bndbox']['xmax']) >= 300:
        print('xmax',float(obj['bndbox']['xmax']))
        print(data['filename'])
      ymax.append(float(obj['bndbox']['ymax']) / height)
      #print('ymin',(1-float(obj['bndbox']['ymin']) / height), height)
      #print('ymin',1080-float(obj['bndbox']['ymin']))
      if float(obj['bndbox']['ymax']) >= 300:
        print('ymax',1079-int(float(obj['bndbox']['ymax'])))
        print(data['filename']) 
      classes_text.append(obj['name'].encode('utf8'))
      classes.append(label_map_dict[obj['name']])
      truncated.append(int(obj['truncated']))
      poses.append(obj['pose'].encode('utf8'))
  
  example = tf.train.Example(features=tf.train.Features(feature={
  'image/height': dataset_util.int64_feature(height),
  'image/width': dataset_util.int64_feature(width),
  'image/filename': dataset_util.bytes_feature(
  data['filename'].encode('utf8')),
  'image/source_id': dataset_util.bytes_feature(
  data['filename'].encode('utf8')),
  'image/key/sha256': dataset_util.bytes_feature(key.encode('utf8')),
  'image/encoded': dataset_util.bytes_feature(encoded_jpg),
  'image/format': dataset_util.bytes_feature('jpeg'.encode('utf8')),
  'image/object/bbox/xmin': dataset_util.float_list_feature(xmin),
  'image/object/bbox/xmax': dataset_util.float_list_feature(xmax),
  'image/object/bbox/ymin': dataset_util.float_list_feature(ymin),
  'image/object/bbox/ymax': dataset_util.float_list_feature(ymax),
  'image/object/class/text': dataset_util.bytes_list_feature(classes_text),
  'image/object/class/label': dataset_util.int64_list_feature(classes),
  'image/object/difficult': dataset_util.int64_list_feature(difficult_obj),
  'image/object/truncated': dataset_util.int64_list_feature(truncated),
  'image/object/view': dataset_util.bytes_list_feature(poses),
  }))
  return example

def create_tf(examples_list, annotations_dir, label_map_dict,dataset_type):
  writer = None
  if not os.path.exists(FLAGS.output_path+"/"+dataset_type):
    os.mkdir(FLAGS.output_path+"/"+dataset_type)
  j = 0
  for idx, example in enumerate(examples_list):
    if idx % 100 == 0:
      print('On image %d of %d', idx, len(examples_list))
      logging.info('On image %d of %d', idx, len(examples_list))
      print((FLAGS.output_path + "/tf_training_" + str(j) + ".record"))
      writer = tf.python_io.TFRecordWriter(FLAGS.output_path +"/"+dataset_type+"/tf_training_" + str(j) + ".record")
      j = j + 1
    path = os.path.join(annotations_dir, os.path.basename(example).replace(".jpg", '.xml'))
    with tf.gfile.GFile(path, 'r') as fid:
      xml_str = fid.read()
    xml = etree.fromstring(xml_str)
    data = dataset_util.recursive_parse_xml_to_dict(xml)['annotation']
    tf_example = dict_to_tf_example(data, FLAGS.data_dir,label_map_dict,FLAGS.ignore_difficult_instances)
    writer.write(tf_example.SerializeToString())

def main(_):
  data_dir = FLAGS.data_dir
  create_trainval_list(data_dir)

  label_map_dict = label_map_util.get_label_map_dict(FLAGS.label_map_path)

  examples_path = os.path.join(data_dir,'trainval.txt')
  annotations_dir = os.path.join(data_dir, FLAGS.annotations_dir)
  examples_list = dataset_util.read_examples_list(examples_path)

  random.seed(42)
  random.shuffle(examples_list)
  num_examples = len(examples_list)
  num_train = int(0.7 * num_examples)
  train_examples = examples_list[:num_train]
  val_examples = examples_list[num_train:]

  create_tf(train_examples, annotations_dir, label_map_dict, "train")
  create_tf(val_examples, annotations_dir, label_map_dict, "val")

if __name__ == '__main__':
  tf.app.run()   

In [ ]:
# now we will downloar the pretrained model of SSD Inception V2 to train it with our new dataset

%%shell
cd /content/pre-trained-model
mkdir pre-trained-model
cd pre-trained-model
wget http://download.tensorflow.org/models/object_detection/ssd_inception_v2_coco_2018_01_28.tar.gz
tar -xvf ssd_inception_v2_coco_2018_01_28.tar.gz

In [ ]:
tf.test.gpu_device_name()

'/device:GPU:0'

In [ ]:
# at this block we will start the training process, notice that this process requires tenorflow 1.x
# we must modify the pipline.config file to suit our training process.
# the following aspects must be changed : 
#     1. num_classes: our number of classes 
#     2. fine_tune_checkpoint: path to pre-trained model checkpoint
#     3. label_map_path: path to .pbtxt file
#     4. input_path: path to the training TFRecord files
#     5. label_map_path: path to the .pbtxt file
#     6. input_path: path to the validation TFRecord files

%%shell
#%tensorflow_version 1.x
export PYTHONPATH=$PYTHONPATH:/content/models/research:/content/models/research/slim

cd models/research/
PIPELINE_CONFIG_PATH=/content/pre-trained-model/pre-trained-model/ssd_inception_v2_coco_2018_01_28/pipeline.config
MODEL_DIR=/content/new_new_defect_detection_model/
NUM_TRAIN_STEPS=10000
SAMPLE_1_OF_N_EVAL_EXAMPLES=1
python object_detection/model_main.py \
  --pipeline_config_path=${PIPELINE_CONFIG_PATH} \
  --model_dir=${MODEL_DIR} \
  --num_train_steps=${NUM_TRAIN_STEPS} \
  --sample_1_of_n_eval_examples=$SAMPLE_1_OF_N_EVAL_EXAMPLES \
  --alsologtostderr

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.



W0815 13:54:47.148649 140282826037120 module_wrapper.py:139] From /content/models/research/object_detection/utils/config_util.py:102: The name tf.gfile.GFile is deprecated. Please use tf.io.gfile.GFile instead.


W0815 13:54:47.151577 140282826037120 module_wrapper.py:139] From /content/models/research/object_detection/model_lib.py:628: The name tf.logging.warning is deprecated. Please use tf.compat.v1.logging.warning instead.

W0815 13:54:47.151721 140282826037120 model_lib.py:629] Forced number of epochs for all eval validations to be 1.

W0815 13:54:47.151840 140282826037120 module_wrapper.py:139] From /content/models/resea

In [ ]:
# Now we have to export the trained model in order to use it later at our locale machine
# Also we have to write the directory of the checkpoint file

%%shell

export PYTHONPATH=$PYTHONPATH:/content/models/research
export PYTHONPATH=$PYTHONPATH:/content/models/research/slim
cd /content/models/research

python object_detection/export_inference_graph.py \
--input_type image_tensor \
--pipeline_config_path /content/pre-trained-model/pre-trained-model/ssd_inception_v2_coco_2018_01_28/pipeline.config \
--trained_checkpoint_prefix /content/new_new_defect_detection_model/model.ckpt-10000 \
--output_directory /content/new_final_defect_detection/final_model

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.



W0815 15:10:40.330280 139778473092992 module_wrapper.py:139] From object_detection/export_inference_graph.py:145: The name tf.gfile.GFile is deprecated. Please use tf.io.gfile.GFile instead.


W0815 15:10:40.337552 139778473092992 module_wrapper.py:139] From /content/models/research/object_detection/exporter.py:402: The name tf.gfile.MakeDirs is deprecated. Please use tf.io.gfile.makedirs instead.


W0815 15:10:40.337812 139778473092992 module_wrapper.py:139] From /content/models/research/object_detection/exporter.py:121: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.


W0815 15:10:40.37131

In [ ]:
import tensorflow

In [ ]:
# Evaluating the model using Tensorboard 

%tensorflow_version 2.x
%load_ext tensorboard
%tensorboard --logdir /content/new_new_defect_detection_model